In [2]:
import sys
import os
from modules.dataset import ImageAnnotations

!git clone https://github.com/CASIA-IVA-Lab/FastSAM.git
os.chdir('FastSAM') 
sys.path.insert(0, '..') # allow you to import modules from sam repo

!pip install -r requirements.txt
# !pip install git+https://github.com/openai/CLIP.git
import torch
import numpy as np
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [3]:
def sam_input_points_from_annotations(annotation:ImageAnnotations, bbox_id:int, include_aux=True):
    """Get input points and labels from an ImageAnnotations object."""
    bbox = next(box for box in annotation.box_annotations if box['id'] == annotation.box_annotations[bbox_id]['id'])
    input_points = []
    input_labels = []
    for point_id in bbox['points_inside']:
        point = next(p for p in annotation.point_annotations if p['id'] == point_id)
        aux_points = []
        if point['is_aux']:
            aux_points.append(point)
        else:
            input_points.append([point['coord_bb'][1], point['coord_bb'][0]])
            input_labels.append(point['is_positive'])
        if include_aux and aux_points:
            for aux_point in aux_points:
                input_points.append([aux_point['coord_bb'][1], aux_point['coord_bb'][0]])
                input_labels.append(point['is_positive'])
    return np.array(input_points), np.array(input_labels).astype(int)

In [4]:
from fastsam import FastSAM, FastSAMPrompt 
import ast
import torch
from PIL import Image
from utils.tools import convert_box_xywh_to_xyxy
import time

def run_fast_sam(
    model=None,
    img_np = None,
    img_path="./images/dogs.jpg",
    imgsz=1024,
    iou=0.9,
    text_prompt=None,
    conf=0.4,
    output="./output/",
    randomcolor=True,
    point_prompt=None,
    point_label=[0],
    box_prompt=[[0,0,0,0]],
    better_quality=False,
    device=None,
    retina=True,
    withContours=False
):
    if device is None:
        device = torch.device(
            "cuda" if torch.cuda.is_available() else 
            "mps" if torch.backends.mps.is_available() else 
            "cpu"
        )
    
    point_prompt = point_prompt
    # box_prompt = convert_box_xywh_to_xyxy(ast.literal_eval(box_prompt))
    box_prompt = box_prompt
    point_label = point_label
    if isinstance(img_np, np.ndarray):
        print(img_np.shape)
        input_img = Image.fromarray(img_np)
        # img_path = "temp.jpg"
        img_path = f'{time.time()}.jpg'
    else:
        input_img = Image.open(img_path)
    # input_img = Image.open(img_path)
    input_img = input_img.convert("RGB")

    everything_results = model(
        input_img,
        device=device,
        # retina_masks=retina,
        imgsz=imgsz,
        # conf=conf,
        # iou=iou    
    )

    bboxes = None
    points = None
    point_label_value = None
    prompt_process = FastSAMPrompt(input_img, everything_results, device=device)
    if box_prompt[0][2] != 0 and box_prompt[0][3] != 0:
        ann = prompt_process.box_prompt(bboxes=box_prompt)
        bboxes = box_prompt
    elif text_prompt is not None:
        ann = prompt_process.text_prompt(text=text_prompt)

    elif point_prompt[0] is not None:
        ann = prompt_process.point_prompt(points=point_prompt, pointlabel=point_label)
        points = point_prompt
        point_label_value = point_label
    else:
        ann = prompt_process.everything_prompt()

    # prompt_process.plot(
    #     annotations=ann,
    #     output_path=output + img_path.split("/")[-1],
    #     bboxes=bboxes,
    #     points=points,
    #     point_label=point_label_value,
    #     withContours=withContours,
    #     better_quality=better_quality,
    # )
    return ann

## Base code for debugging
# model_path="./weights/FastSAM-X.pt"
# model = FastSAM(model_path)
# annots = run_fast_sam(
#     model=model,
#     img_path = 'images/dogs.jpg', # "../datasets/images/CSV_1865.jpg",
#     point_prompt=[[520,360],[330,410]],
#     point_label=[1,1],
#     # output="./output/",
# )
# annots

In [5]:
import cv2
def get_fastsam_prediction_point(fastsam_model, annotations:ImageAnnotations, jsons_folder='../datasets/supervisely_annotations/'
                       , wgisd_folder='../datasets/wgisd_annotations/', include_aux=True, wgisd_n_points=3):
    """Get a prediction from a sam_predictor object."""
    annotations.load_image('../datasets/images/' + annotations.image_name)

    if annotations.image_name.startswith('DSC'):
            annotations.read_supervisely(jsons_folder + annotations.image_name + '.json')
    elif annotations.image_name.startswith('SYH') or annotations.image_name.startswith('CSV'):
        sufx = f'-{wgisd_n_points}point' if wgisd_n_points==1 else f'-{wgisd_n_points}points'
        annotations.read_wgisd(wgisd_folder + annotations.image_name.replace('.jpg', '.npz'), excel_sufx=sufx)
    
    masks_list = []
    for id, bb in enumerate(annotations.box_annotations): 
        print(bb)
        image = annotations.bb_image_2_np(bb)
        input_points, input_labels = sam_input_points_from_annotations(annotations, id, include_aux=include_aux)
        print(input_points, input_labels)
        mask = run_fast_sam(
            model=fastsam_model,
            img_np=image,
            point_prompt=input_points[:, [1, 0]], # As standard SAM expects (y, x) coordinates, we need to swap them
            point_label=input_labels,
            output="./output/",)
        if not isinstance(mask, list):
            mask = cv2.resize(mask.astype(np.uint8)[0], (image.shape[1], image.shape[0]), interpolation=cv2.INTER_AREA)
        else: # cria un novo array com as dimensões da imagem
            mask = np.zeros((image.shape[0], image.shape[1]), dtype=np.uint8)
        masks_list.append(mask)
    return masks_list

def _convert_coordinates(coords):
    x1, y1 = coords[0]
    x2, y2 = coords[1]
    w = x2 - x1
    h = y2 - y1
    return [x1, y1, w, h]

def get_fastsam_prediction_bbox(fastsam_model, annotations:ImageAnnotations, jsons_folder='../datasets/supervisely_annotations/'
                       , wgisd_folder='../datasets/wgisd_annotations/'):
    """Get a prediction from a sam_predictor object."""
    annotations.load_image('../datasets/images/' + annotations.image_name)

    if annotations.image_name.startswith('DSC'):
        annotations.read_supervisely(jsons_folder + annotations.image_name + '.json')
    elif annotations.image_name.startswith('SYH') or annotations.image_name.startswith('CSV'):
        annotations.read_wgisd(wgisd_folder + annotations.image_name.replace('.jpg', '.npz'))

    mask = run_fast_sam(model=fastsam_model,
                img_np=annotations.image,
                imgsz=2048,
                box_prompt=[_convert_coordinates(bb['coords']) for bb in annotations.box_annotations],
                output="./output/")
    return mask

def save_fastsam_predictions(imgs, output_folder, model, prediction_name, include_aux=True,
                                                    jsons_folder='../datasets/supervisely_annotations/',
                                                        wgisd_folder='../datasets/wgisd_annotations/', wgisd_n_points=None
                                                        , bounding_boxes=False):
    for img in imgs:
        anot = ImageAnnotations(img)
        print ('Processing', anot.image_name)
        if bounding_boxes:
            masks = get_fastsam_prediction_bbox(model, anot, jsons_folder, wgisd_folder)
            anot.image_pred[prediction_name] = masks
        else:
            masks = get_fastsam_prediction_point(model, anot, jsons_folder, wgisd_folder, include_aux, wgisd_n_points)
            anot.reconstruct_prediction_mask(masks, prediction_name)
        dados = { 
                    'full': (anot.image_pred[prediction_name]).astype(np.uint8),
                    'bbs': {i:(pred[:,:]).astype(np.uint8) for i, pred in enumerate(masks)}
        }
        # dados = (anot.image_pred[prediction_name] > 0.45).astype(np.int8)
        np.savez_compressed(f'{output_folder}/{anot.image_name}_{prediction_name}.npz', **dados, allow_pickle=True)
        print(f'{anot.image_name} annotation saved.')

all_jpgs = os.listdir('../datasets/images/')
wgisd_csv = [img for img in all_jpgs if img.startswith('CSV')]
wgisd_syh = [img for img in all_jpgs if img.startswith('SYH')]
supervisely = [img for img in all_jpgs if img.startswith('DSC')]
model = FastSAM('./weights/FastSAM-X.pt')


In [6]:
import time

start = time.time()
save_fastsam_predictions(supervisely[:1], '../datasets/fastsam_predictions/', model, 'fastsam_bbs', bounding_boxes=True)
print('Tempo de execução 3 pontos:', time.time() - start, 'segundos')

Processing DSC_0109.JPG
(4000, 6016, 3)



0: 1376x2048 300 objects, 1668.6ms
Speed: 201.3ms preprocess, 1668.6ms inference, 30036.3ms postprocess per image at shape (1, 3, 2048, 2048)


(1, 1376, 2048)
float32
[[[          0           0           0 ...           0           0           0]
  [          0           0           0 ...           0           0           0]
  [          0           0           0 ...           0           0           0]
  ...
  [          0           0           0 ...           0           0           0]
  [          0           0           0 ...           0           0           0]
  [          0           0           0 ...           0           0           0]]]
DSC_0109.JPG annotation saved.
Tempo de execução 3 pontos: 77.5661404132843 segundos


In [10]:
import time

start = time.time()
save_fastsam_predictions(supervisely, '../datasets/fastsam_predictions/', model, 'fastsam_3_points', include_aux=True, wgisd_n_points=3)
print('Tempo de execução 3 pontos:', time.time() - start, 'segundos')

Processing DSC_0109.JPG


{'class': 'caixa', 'coords': [[616, 2095], [1124, 2410]], 'id': 0, 'points_inside': [59, 60, 66]}
[[235 223]
 [100  39]
 [214 346]] [0 1 1]
(315, 508, 3)


0: 640x1024 26 objects, 156.1ms
Speed: 10.0ms preprocess, 156.1ms inference, 7.9ms postprocess per image at shape (1, 3, 1024, 1024)


0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
0 [449, 477]
1 [78, 203]
2 [697, 434]
{'class': 'c


0: 544x1024 103 objects, 141.0ms
Speed: 9.0ms preprocess, 141.0ms inference, 15.0ms postprocess per image at shape (1, 3, 1024, 1024)


...

{'class': 'caixa', 'coords': [[5239, 1797], [5607, 2345]], 'id': 12, 'points_inside': [2, 3, 41]}
[[458 151]
 [108 159]
 [317 122]] [1 1 1]
(548, 368, 3)


0: 1024x704 57 objects, 178.9ms
Speed: 10.1ms preprocess, 178.9ms inference, 11.0ms postprocess per image at shape (1, 3, 1024, 1024)


0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]
2 [233, 592]
0 [288, 855]
1 [304, 201]


0: 1024x576 37 objects, 154.0ms
Speed: 8.0ms preprocess, 154.0ms inference, 8.0ms postprocess per image at shape (1, 3, 1024, 1024)


0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]
2 [505, 164]
0 [416, 501]
1 [556, 728]

In [8]:
save_fastsam_predictions(wgisd_csv, '../datasets/fastsam_predictions/', model, 'fastsam_1_points', include_aux=False, wgisd_n_points=1)
print('Tempo de execução 1 ponto:', time.time() - start, 'segundos')

Processing CSV_1865.jpg


WGisd annotations loaded.
{'coords': [[1051, 706], [1317, 1228]], 'id': 0, 'points_inside': [0]}
[[     243.34      107.59]] [1]
(522, 266, 3)


0: 1024x544 114 objects, 153.0ms
Speed: 8.0ms preprocess, 153.0ms inference, 14.0ms postprocess per image at shape (1, 3, 1024, 1024)



0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]
0 [220, 477]

0: 1024x704 128 objects, 172.0ms
Speed: 9.9ms preprocess, 172.0ms inference, 24.0ms postprocess per image at shape (1, 3, 1024, 1024)


...

0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
0 [318, 559]
{'coords': [[951, 622], [1110, 792]], 'id': 10, 'points_inside': [10]}
[[     99.282      78.872]] [1]
(170, 159, 3)



0: 1024x960 51 objects, 238.0ms
Speed: 17.0ms preprocess, 238.0ms inference, 17.0ms postprocess per image at shape (1, 3, 1024, 1024)


0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
0 [476, 598]
{'coords': [[1797, 564], [1929, 663]], 'id': 11, 'points_inside': [11]}
[[     44.545      68.909]] [1]
(99, 132, 3)



0: 768x1024 24 objects, 185.0ms
Speed: 11.0ms preprocess, 185.0ms inference, 7.0ms postprocess per image at shape (1, 3, 1024, 1024)


0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
0 [534, 345]
(1536, 2048)
float64
[[          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 ...
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]]
CSV_20180427_144723166_HDR.jpg annotation saved.
Tempo de execução 1 ponto: 2665.6079754829407 segundos


In [9]:
save_fastsam_predictions(supervisely, '../datasets/fastsam_predictions/', model, 'fastsam_1_points', include_aux=False, wgisd_n_points=1)
print('Tempo de execução 1 ponto:', time.time() - start, 'segundos')

Processing DSC_0109.JPG


{'class': 'caixa', 'coords': [[616, 2095], [1124, 2410]], 'id': 0, 'points_inside': [59, 60, 66]}
[[214 346]] [1]
(315, 508, 3)


0: 640x1024 26 objects, 157.0ms
Speed: 10.0ms preprocess, 157.0ms inference, 8.0ms postprocess per image at shape (1, 3, 1024, 1024)



0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
0 [697, 434]
{'class': 'caixa', 'coords': [[1660, 2207], [2148, 2453]], 'id': 1, 'points_inside': [30, 31, 32]}
[[ 85 258]] [1]
(246, 488, 3)


0: 544x1024 103 objects, 139.0ms
Speed: 8.0ms preprocess, 139.0ms inference, 13.0ms postprocess per image at shape (1, 3, 1024, 1024)


...

{'class': 'caixa', 'coords': [[5239, 1797], [5607, 2345]], 'id': 12, 'points_inside': [2, 3, 41]}
[[317 122]] [1]
(548, 368, 3)


0: 1024x704 57 objects, 178.1ms
Speed: 11.0ms preprocess, 178.1ms inference, 9.9ms postprocess per image at shape (1, 3, 1024, 1024)


0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
0 [233, 592]
{'class': 'caixa', 'coords': [[5722, 1586], [6015, 2127]], 'id': 13, 'points_inside': [0, 1, 39]}
[[ 87 257]] [1]
(541, 293, 3)



0: 1024x576 37 objects, 153.0ms
Speed: 10.0ms preprocess, 153.0ms inference, 11.0ms postprocess per image at shape (1, 3, 1024, 1024)


0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
0 [505, 164]
(4000, 6016)
float64
[[          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 ...
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]
 [          0           0           0 ...           0           0           0]]
DSC_0342.JPG annot